In [1]:
#import necessary libraries

import re
import argparse

In [2]:
#use argparse to define command lines
parser=argparse.ArgumentParser()
parser.add_argument("-f","--filename",
                   help="name of the input file")
parser.add_argument("-imz", "--minimum_mass_to_charge_ratio_range",
                    help="the minimum number of mass-to-charge of the peptide fragment", type=float,default=1000)
parser.add_argument("-amz", "--maximum_mass_to_charge_ratio_range",
                    help="the maximum number of mass-to-charge of the peptide fragment", type=float,default=1500)
parser.add_argument("-w", "--window_size",
                    help="size of the sliding window", type=float, default=0.1)
parser.add_argument("-s", "--step_size",
                    help="size of steps the sliding window slides(must be smaller than window size)", type=float, default=0.05)
parser.add_argument("-m", "--match_pattern",
                    help="how the input amino acid matches the sequence", choices=['start with','contain'])
parser.add_argument("-p", "--peptide_matches_sequence",
                    help="input peptide matching the sequence",
                    choices=['K','N','R','T','S','I','M','Q','H','P','L','E','D','A','G','V','Y','S','C','W','F'])
args = parser.parse_args()

usage: __main__.py [-h] [-f FILENAME]
                   [-imz MINIMUM_MASS_TO_CHARGE_RATIO_RANGE]
                   [-amz MAXIMUM_MASS_TO_CHARGE_RATIO_RANGE] [-w WINDOW_SIZE]
                   [-s STEP_SIZE] [-m {start with,contain}]
                   [-p {K,N,R,T,S,I,M,Q,H,P,L,E,D,A,G,V,Y,S,C,W,F}]
__main__.py: error: unrecognized arguments: --matplotlib=inline -c %config InlineBackend.figure_formats = set(['retina'])
import matplotlib; matplotlib.rcParams['figure.figsize'] = (12, 7)


SystemExit: 2

/usr/local/lib/python3.8/dist-packages/IPython/core/interactiveshell.py:3426: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [14]:


filename=input('Enter name of the peptide ion masses file: ')  # input file name
protein_name=[]                                 #list of useful elements
mass_to_charge=[]
sequence=[]
create_file="task4.csv"
output=open(create_file,'w')

def readfile(filename):                            #define a function to read file and store data
    readfile=open(filename,'r')
    lines=readfile.readlines()
    for line in lines:
        data=line.split()
        protein_name.append(data[0])
        mass_to_charge.append(data[2])
        sequence.append(data[5])

min_mz=float(input("the minimum mass to charge ratio is:"))
max_mz=float(input("the maximum mass to charge ratio is:"))
def count_num(min_mz,max_mz):      #define a function to count number of peptides
    count_pep=0
    list1=[]
    list2=[]
    list3=[]
    global output
    for m in mass_to_charge:     #use defined list mass_to_charge, loops and if statement to count
        mz=float(m)
        if ((min_mz<mz)&(mz<max_mz)):
            count_pep+=1
    if count_pep==1:
        print("There is ",count_pep," peptide within the mass to charge range of ", min_mz," and ",max_mz)
    elif count_pep!=0:
        print("There are ",count_pep," peptides within the mass to charge range of ", min_mz," and ",max_mz)
    list1.append(min_mz)
    list2.append(max_mz)
    list3.append(count_pep)
    for i in zip(list1,list2,list3):
        output.write(str(i[0])+'\t'+str(i[1])+'\t'+str(i[2])+'\n')
    return count_pep

def find_protein():            #define a function to find unique protein
    new_pr=list(set(protein_name))  #remove the duplication of protein
    new_pr.sort(key=protein_name.index)
    mz_num={}
    rep_mz=[]
    i_mz=[]
    rep_pr=[]
    uni_pr=[]
    list1=[]
    list2=[]
    global output
    for i in range(len(mass_to_charge)):      #record the frequency of mass_to_charge
        if mass_to_charge[i] in mz_num:
            mz_num[mass_to_charge[i]]+=1
        else:
            mz_num[mass_to_charge[i]]=1
    for key in mz_num:                  #a list containing all duplicated m/z
        if mz_num[key]!=1:
            rep_mz.append(key)
    for mz in rep_mz:                   #find the index of duplicated m/z and store correspond protein name
        i_mz.append(mass_to_charge.index(mz))
        for im in i_mz:
            rep_pr.append(protein_name[im])
    new_rep=list(set(rep_pr))
    new_rep.sort(key=rep_pr.index)  #remove the duplication of duplicated protein name
    for pr in new_pr:
        if pr not in new_rep:
            uni_pr.append(pr)   #put element(s) in unique 
    if len(uni_pr)==1:
        print(" ".join(str(i) for i in uni_pr)," has been unambiguously identified in all proteins")
    else:
        print(",".join(str(i) for i in uni_pr)," have been unambiguously identified in all proteins")
    list1.append("unique proteins:")
    for i in uni_pr:
        list1.append(" ")
    list2.append(uni_pr[i] for i in uni_pr)
    for i in zip(list1,list2):
        output.write(str(i[0])+'\t'+str(i[1])+'\n')

pep_find=input("looking for peptide: ")             #input matching peptide and pattern
match_pattern=input("the sequences start with or contain the peptide?(enter 'start with' or 'contain') ")
def match_peptide(pep_find,match_pattern):             #define a function to match peptide
    match=[]
    list1=[]
    list2=[]
    global output
    if match_pattern=="start with":                #differentiate different match pattern
        for s in sequence:
            if s.startswith(pep_find):
                match.append(s)
        if len(match)==0:
            print("There is no sequence starts with ",pep_find," in all peptides.")
    else:
        for s in sequence:
            if pep_find in s:
                match.append(s)
        if len(match)==0:
            print("There is no sequence contains ",pep_find," in all peptides.")
    if len(match)==1:
        print("There is ",len(match)," sequence ",match_pattern, pep_find," in all peptides.")
    else:
        print("There are ",len(match)," sequences ",match_pattern, pep_find," in all peptides.")
    list1.append("number of matched sequence")
    list2.append(len(match))
    for i in zip(list1,list2):
        output.write(str(i[0])+'\t'+str(i[1])+'\n')


readfile(filename)
window_size=float(input("the size of window is: "))
step_size=float(input("the size of step is(must be smaller than window size):"))
count_num(min_mz,max_mz)
while min_mz<max_mz:
    window=min_mz+window_size
    count_num(min_mz,window)
    min_mz+=step_size
find_protein()
match_peptide(pep_find,match_pattern)
output.close()

Enter name of the peptide ion masses file:  dummy.pepmasses

the minimum mass to charge ratio is: 1000

the maximum mass to charge ratio is: 1200

looking for peptide:  K

the sequences start with or contain the peptide?(enter 'start with' or 'contain')  contain

the size of window is:  5

the size of step is(must be smaller than window size): 3

There are  34  peptides within the mass to charge range of  1000.0  and  1200.0
There are  2  peptides within the mass to charge range of  1000.0  and  1005.0
There is  1  peptide within the mass to charge range of  1003.0  and  1008.0
There is  1  peptide within the mass to charge range of  1006.0  and  1011.0
There is  1  peptide within the mass to charge range of  1009.0  and  1014.0
There are  2  peptides within the mass to charge range of  1012.0  and  1017.0
There is  1  peptide within the mass to charge range of  1015.0  and  1020.0
There is  1  peptide within the mass to charge range of  1024.0  and  1029.0
There is  1  peptide within the mass to charge range of  1027.0  and  1032.0
There are  3  peptides within the mass to charge range of  1030.0  and  1035.0
There are  3  peptides within the mass to charge range of  1033.0  and  1038.0
There is  1  peptide within the mass to charge range of  1036.0  and  1041.0
There is  1  peptide within the mass to charge range of  1039.0  

In [0]:
import pandas as pd
list=[[1,2,3],[4,5,6],[7,8,9]]
column=['column1','column2','column3']
test=pd.DataFrame(columns=column,data=list)
test.to_csv

In [8]:
list1=[1,2,3,4,5]
list2=[4,5,6]
list3=[]
list3.append(list1)
list3.append(list2)
for i in list1:
    print(list1[i],list2[i])
print(list3)

2 5
3 6


IndexError: list index out of range

SyntaxError: invalid character in identifier (<ipython-input-2-858119bd1d17>, line 17)

In [0]:
#import necessary libraries
import argparse

#use argparse to define command lines
parser=argparse.ArgumentParser()
parser.add_argument("-f","--filename",
                    help="name of the input file",required=True)
parser.add_argument("-i", "--minimum_mass_to_charge_ratio_range",
                    help="the minimum range of mass-to-charge of the peptide fragment", type=float,default=1000)
parser.add_argument("-a", "--maximum_mass_to_charge_ratio_range",
                    help="the maximum range of mass-to-charge of the peptide fragment", type=float,default=1500)
parser.add_argument("-w", "--window_size",
                    help="size of the sliding window", type=float, default=1)
parser.add_argument("-s", "--step_size",
                    help="size of steps the sliding window slides(must be smaller than window size)", type=float, default=0.5)
parser.add_argument("-m", "--match_pattern",
                    help="how the input amino acid matches the sequence", choices=['start with','contain']，default='contain')
parser.add_argument("-p", "--amino_acid_matches_sequence",
                    help="input amino acid matching the sequence",
                    choices=['K','N','R','T','S','I','M','Q','H','P','L','E','D','A','G','V','Y','S','C','W','F'], required=True)
parser.add_argument("-c","--create_file",
                    help="name of the output file",required=True)
args = parser.parse_args()

filename=args.filename
min_mz=args.minimum_mass_to_charge_ratio_range
max_mz=args.maximum_mass_to_charge_ratio_range
window_size=args.window_size
step_size=args.step_size
match_pattern=args.match_pattern
pep_find=args.peptide_matches_sequence
create_file=args.create_file

protein_name=[]                                 #lists of useful elements
mass_to_charge=[]
sequence=[]
create_file="task4.csv"                           #create a file to store the output
output=open(create_file,'w')

def readfile(filename):                            #define a function to read file and store data
    readfile=open(filename,'r')
    lines=readfile.readlines()
    for line in lines:
        data=line.split()                        #use split to handle the data
        protein_name.append(data[0])
        mass_to_charge.append(data[2])
        sequence.append(data[5])


def count_num(min_mz,max_mz):      #define a function to count number of peptides
    count_pep=0
    list1=[]                #use lists to store output data
    list2=[]
    list3=[]
    global output
    for m in mass_to_charge:     #use defined list mass_to_charge, loops and if statement to count
        mz=float(m)
        if ((min_mz<mz)&(mz<max_mz)):
            count_pep+=1
    if count_pep==1:
        print("mass range:", "minimum:",min_mz,", maximum:",max_mz," count:",count_pep)
    elif count_pep!=0:
        print("There are ",count_pep," peptides within the mass to charge range of ", min_mz," and ",max_mz)
    list1.append(min_mz)
    list2.append(max_mz)
    list3.append(count_pep)
    for i in zip(list1,list2,list3):
        output.write(str(i[0])+'\t'+str(i[1])+'\t'+str(i[2])+'\n')
    return count_pep

def count_num_ppm(min_mz,ppm):      #define a function to count number of peptides
    count_pep=0
    window = min_mz * ppm / 1000000.0
    max_mz = min_mz + window
    for m in mass_to_charge:     #use defined list mass_to_charge, loops and if statement to count
        mz=float(m)
        if ((min_mz<mz)&(mz<max_mz)):
            count_pep+=1
    if count_pep==1:
        print("mass range:", "minimum:",min_mz,", maximum:",max_mz," count:",count_pep)
    elif count_pep!=0:
        print("There are ",count_pep," peptides within the mass to charge range of ", min_mz," and ",max_mz)
    return count_pep

def find_protein():            #define a function to find unique protein
    new_pr=list(set(protein_name))  #remove the duplication of protein
    new_pr.sort(key=protein_name.index)
    mz_num={}
    rep_mz=[]
    i_mz=[]
    rep_pr=[]
    uni_pr=[]
    list1=[]
    list2=[]
    global output
    for i in range(len(mass_to_charge)):      #record the frequency of mass_to_charge
        if mass_to_charge[i] in mz_num:
            mz_num[mass_to_charge[i]]+=1
        else:
            mz_num[mass_to_charge[i]]=1
    for key in mz_num:                  #a list containing all duplicated m/z
        if mz_num[key]!=1:
            rep_mz.append(key)
    for mz in rep_mz:                   #find the index of duplicated m/z and store correspond protein name
        i_mz.append(mass_to_charge.index(mz))
        for im in i_mz:
            rep_pr.append(protein_name[im])
    new_rep=list(set(rep_pr))
    new_rep.sort(key=rep_pr.index)  #remove the duplication of duplicated protein name
    for pr in new_pr:
        if pr not in new_rep:
            uni_pr.append(pr)   #put element(s) in unique 
    if len(uni_pr)==1:
        print(" ".join(str(i) for i in uni_pr)," has been unambiguously identified in all proteins")
    else:
        print(",".join(str(i) for i in uni_pr)," have been unambiguously identified in all proteins")
    list1.append("unique proteins:")
    for i in uni_pr:
        list1.append(" ")
    list2.append(uni_pr[i] for i in uni_pr)
    for i in zip(list1,list2):
        output.write(str(i[0])+'\t'+str(i[1])+'\n')


def match_peptide(pep_find,match_pattern):             #define a function to match peptide
    match=[]
    list1=[]
    list2=[]
    global output
    if match_pattern=="start with":                #differentiate different match pattern
        for s in sequence:
            if s.startswith(pep_find):
                match.append(s)
        if len(match)==0:
            print("There is no sequence starts with ",pep_find," in all peptides.")
    else:
        for s in sequence:
            if pep_find in s:
                match.append(s)
        if len(match)==0:
            print("There is no sequence contains ",pep_find," in all peptides.")
    if len(match)==1:
        print("There is ",len(match)," sequence ",match_pattern, pep_find," in all peptides.")
    else:
        print("There are ",len(match)," sequences ",match_pattern, pep_find," in all peptides.")
    list1.append("number of matched sequence")
    list2.append(len(match))
    for i in zip(list1,list2):
        output.write(str(i[0])+'\t'+str(i[1])+'\n')

readfile(filename)              #main code starts here
count_num(min_mz,max_mz)
while min_mz<max_mz:
    window=min_mz+window_size
    if error_type == 0:
        count_num(min_mz,window)  # if you want to implement ppm error then I would use a new function
    else:  # ppm error comes here
        count_num_ppm(min_mz,ppm)  # 
    
    min_mz+=step_size
find_protein()
match_peptide(pep_find,match_pattern)
output.close()

In [19]:
dic1={'a':1,'b':3,'c':5}
dic2={'a':2,'b':2,'c':4,'d':4}
list1=[1,2,3,4,5]
list2=['a','b','c','d','b','c','d','e']
list3=[1,2,2,2,2,3,3,4]
dic3={}
for x in dic1:
    if dic1[x]!=1:
        dic3[x]=[]
for y in dic3.keys():
    for index,nums in enumerate(list2):
        if nums==y:
            dic3[y].append(list3[index])
print(dic3)
for x in dic3:
    list4=[]
    list6=[]
    for x in dic3[x]:
        list4.append(x)
        list5=[]
        list5=set(list4)
        if len(list5)!=1:
            prit
    print(list6)

{'b': [2, 2], 'c': [2, 3]}
[]
[3]


In [40]:
readfile=input("filename:")
file=open(readfile,'r')
next(file)
mz=[]
i=1000.0
y=[]
x=[]
output1=input("outname")
output=open(output1,'w')
lines=file.readlines()
for line in lines:
    print(line)
    data=line.split()
    mz.append(data[3])
def count_num(a):
    sum1=0
    for m in mz:
        if float(m)>a and float(m)<a+5:
            sum1+=1
    y.append(sum1)
    x.append(a)
while i<1500:
    count_num(i)
    i=i+5
for z in zip(x,y):
    output.writelines([str(z[0]),'\t',str(z[1]),'\n'])

filename: task_3_output_GluC_no_missed.mass

outname refresh.mass

I.claudius_F1_1_340_1_peptide	number	1	3154.6498000000006	0	MAIKIGINGFGRIGRIVFRAAQHRDDIE

I.claudius_F1_1_340_1_peptide	number	2	1185.3241	0	VVGINDLIDVE

I.claudius_F1_1_340_1_peptide	number	3	2384.6417	0	YMAYMLKYDSTHGRFDGTVE

I.claudius_F1_1_340_1_peptide	number	4	1913.1801000000003	0	VKDGNLVVNGKTIRVTAE

I.claudius_F1_1_340_1_peptide	number	5	1910.0914000000005	0	RDPANLNWGAIGVDIAVE

I.claudius_F1_1_340_1_peptide	number	6	966.0428	0	ATGLFLTDE

I.claudius_F1_1_340_1_peptide	number	7	6299.184499999999	0	TARKHITAGAKKVVLTGPSKDATPMFVRGVNFNAYAGQDIVSNASCTTNCLAPLARVVHE

I.claudius_F1_1_340_1_peptide	number	8	8591.745600000002	0	TFGIKDGLMTTVHATTATQKTVDGPSAKDWRGGRGASQNIIPSSTGAAKAVGKVLPALNGKLTGMAFRVPTPNVSVVDLTVNLE

I.claudius_F1_1_340_1_peptide	number	9	1819.0207	0	KPASYDAIKQAIKDAAE

I.claudius_F1_1_340_1_peptide	number	10	751.7846000000001	0	GKTFNGE

I.claudius_F1_1_340_1_peptide	number	11	979.1277000000001	0	LKGVLGYTE

I.claudius_F1_1_340_1_peptide	number	12	4157.4779	0	DAVVSTDFNGCALTSVFDADAGIA

I.claudius_F1_98_395_220730_peptide	number	2	502.56180000000006	0	KNIE

I.claudius_F1_98_395_220730_peptide	number	3	2678.8569	0	IAQKVNDIDVIVTGDSHYLYGNDE

I.claudius_F1_98_395_220730_peptide	number	4	1330.6145999999999	0	LRSLKLPVIYE

I.claudius_F1_98_395_220730_peptide	number	5	520.5754000000001	0	YPLE

I.claudius_F1_98_395_220730_peptide	number	6	1493.6820000000002	0	FKNPNGDPVFVME

I.claudius_F1_98_395_220730_peptide	number	7	1882.0765000000001	0	GWAYSAVVGDLGVKFSPE

I.claudius_F1_98_395_220730_peptide	number	8	2758.2467	0	GIASITRKIPHVLMSSHKLQVKNAE

I.claudius_F1_98_395_220730_peptide	number	9	619.6667	0	GKWTE

I.claudius_F1_98_395_220730_peptide	number	10	533.5295000000001	0	LTGDE

I.claudius_F1_98_395_220730_peptide	number	11	3797.3586	0	RKKALDTLKSMKSISLDDHDAKTDMLISKYKSE

I.claudius_F1_98_395_220730_peptide	number	12	858.9394000000001	0	KDRLAQE

I.claudius_F1_98_395_220730_peptide	number	13	2594.8978	0	IVGVITGSAMPGGSANRIPNKAGSNPE

I.claudius_F1_98_395_220730_peptide	number	14	1064.19

I.claudius_F1_182_431_407629_peptide	number	8	501.57370000000003	0	LLQE

I.claudius_F1_182_431_407629_peptide	number	9	850.9554000000002	0	KIDFLSE

I.claudius_F1_182_431_407629_peptide	number	10	1890.1846000000003	0	VIKLALGRSQTLDSIFE

I.claudius_F1_182_431_407629_peptide	number	11	402.4461	0	RVE

I.claudius_F1_182_431_407629_peptide	number	12	1314.5738	0	SIKIQLKRLSE

I.claudius_F1_182_431_407629_peptide	number	13	1410.5485	0	TNIVGYCYWYE

I.claudius_F1_182_431_407629_peptide	number	14	2569.8682999999996	0	GNGRQFGLHITPLTVADKFGAQLE

I.claudius_F1_182_431_407629_peptide	number	15	346.3795	0	AKE

I.claudius_F1_182_431_407629_peptide	number	16	1209.3471	0	AAWIFTSATLE

I.claudius_F1_182_431_407629_peptide	number	17	1677.8809000000003	0	VGGTFNHFCQRLGIE

I.claudius_F1_182_431_407629_peptide	number	18	1784.9612	0	NATQKILYSPFNYPE

I.claudius_F1_182_431_407629_peptide	number	19	2706.0593	0	QSLLCVPRYLPNTNQMNTLNSLGE

I.claudius_F1_182_431_407629_peptide	number	20	796.0060000000001	0	ILLPVIE

I.claud

...

I.claudius_F2_83_468_208101_peptide	number	21	532.5481	0	SARAE

I.claudius_F2_83_468_208101_peptide	number	22	641.7121000000001	0	FVFTE

I.claudius_F2_83_468_208101_peptide	number	23	147.1293	0	E

I.claudius_F2_83_468_208101_peptide	number	24	1130.2486999999999	0	FYQGLFGLGE

I.claudius_F2_83_468_208101_peptide	number	25	262.2167	0	DE

I.claudius_F2_83_468_208101_peptide	number	26	1992.2350999999999	0	KLDDAYWQQLIKVRSE

I.claudius_F2_83_468_208101_peptide	number	27	728.8374000000001	0	VNRVLE

I.claudius_F2_83_468_208101_peptide	number	28	859.9274	0	ISRNNKE

I.claudius_F2_83_468_208101_peptide	number	29	544.5984000000001	0	IGGGLE

I.claudius_F2_83_468_208101_peptide	number	30	218.2072	0	AE

I.claudius_F2_83_468_208101_peptide	number	31	909.9366000000001	0	VTVYANDE

I.claudius_F2_83_468_208101_peptide	number	32	1247.4	0	YRALLAQLGNE

I.claudius_F2_83_468_208101_peptide	number	33	1934.2803999999999	0	LRFVLITSKVDVKSLSE

I.claudius_F2_83_468_208101_peptide	number	34	944.9823000000001	0	KPADLAD

I.claudius_F2_170_412_437117_peptide	number	15	433.45680000000004	0	TKGE

I.claudius_F2_171_157_439633_peptide	number	1	4111.8497	0	MVQPRTVSVGKKSLIWIPFFGILYWVTGNIFLDRE

I.claudius_F2_171_157_439633_peptide	number	2	2140.3871999999997	0	NRTKAHNTMSQLARRINE

I.claudius_F2_171_157_439633_peptide	number	3	1251.4069000000002	0	DNLSIWMFPE

I.claudius_F2_171_157_439633_peptide	number	4	5587.4053	0	GTRNRGRGLLPFKTGAFHAAISAGVPIIPVVCSSTHNKINLNRWDNGKVICE

I.claudius_F2_171_157_439633_peptide	number	5	3085.4439999999995	0	IMDPIDVSGYTKDNVRDLAAYCHDLME

I.claudius_F2_171_157_439633_peptide	number	6	615.7228	0	KRIAE

I.claudius_F2_171_157_439633_peptide	number	7	375.37430000000006	0	LDE

I.claudius_F2_171_157_439633_peptide	number	8	147.1293	0	E

I.claudius_F2_171_157_439633_peptide	number	9	501.57700000000006	0	IAKGN

I.claudius_F2_172_153_440582_peptide	number	1	690.8505	0	MWLIE

I.claudius_F2_172_153_440582_peptide	number	2	262.2167	0	DE

I.claudius_F2_172_153_440582_peptide	number	3	2715.0827	0	QSLK

I.claudius_F2_268_118_659211_peptide	number	10	147.1293	0	E

I.claudius_F2_268_118_659211_peptide	number	11	712.8380000000001	0	RKPLAE

I.claudius_F2_268_118_659211_peptide	number	12	246.2604	0	VE

I.claudius_F2_268_118_659211_peptide	number	13	637.5958	0	NNDFE

I.claudius_F2_268_118_659211_peptide	number	14	333.29460000000006	0	DAE

I.claudius_F2_268_118_659211_peptide	number	15	147.1293	0	E

I.claudius_F2_269_150_660134_peptide	number	1	4892.743500000001	0	MQVILLDKIVHLGQVGDQVNVKSGFARNFLIPQGKAVMATKANIE

I.claudius_F2_269_150_660134_peptide	number	2	431.4425	0	HFE

I.claudius_F2_269_150_660134_peptide	number	3	601.6565	0	ARRAE

I.claudius_F2_269_150_660134_peptide	number	4	260.2869	0	LE

I.claudius_F2_269_150_660134_peptide	number	5	1470.5873000000001	0	ATAAANLAAAQARAAE

I.claudius_F2_269_150_660134_peptide	number	6	1518.6651000000002	0	VTALGSVTIASKAGDE

I.claudius_F2_269_150_660134_peptide	number	7	1505.6744999999999	0	GRLFGAITTRDVAE

I.claudius_F2_269_150_660134_peptide	number	8	1244

I.claudius_F2_393_52_911422_peptide	number	1	5949.319000000004	0	MVARFLICYLWMNKSKISSIDYRIMAIFLKSRQCSILNTLILILGQISILL

I.claudius_F2_394_248_911757_peptide	number	1	2583.055700000001	0	MINIIFLHGLLGTKNDWQKVIE

I.claudius_F2_394_248_911757_peptide	number	2	2492.8056	0	NLPHFNCIALDLPFHGQAKDLE

I.claudius_F2_394_248_911757_peptide	number	3	608.6408	0	VTNFE

I.claudius_F2_394_248_911757_peptide	number	4	420.3719	0	DSAE

I.claudius_F2_394_248_911757_peptide	number	5	4107.706899999999	0	YLAQQIKSAVKNGPYFLVGYSLGGRIALYYALQAQLE

I.claudius_F2_394_248_911757_peptide	number	6	1128.2793	0	RSNLQGVILE

I.claudius_F2_394_248_911757_peptide	number	7	1017.0912000000001	0	GANLGLKTDE

I.claudius_F2_394_248_911757_peptide	number	8	147.1293	0	E

I.claudius_F2_394_248_911757_peptide	number	9	2315.5678	0	KQARFQQDFAWAQRFMQE

I.claudius_F2_394_248_911757_peptide	number	10	331.32180000000005	0	SPE

I.claudius_F2_394_248_911757_peptide	number	11	2205.4241	0	KVLNDWYQQPVFSHLTTE

I.claudius_F2_394_248_911757_peptide	nu

I.claudius_F2_535_478_1210846_peptide	number	2	1703.9730000000002	0	VVPILNKIDLPAADPE

I.claudius_F2_535_478_1210846_peptide	number	3	473.524	0	RVAE

I.claudius_F2_535_478_1210846_peptide	number	4	147.1293	0	E

I.claudius_F2_535_478_1210846_peptide	number	5	260.2869	0	IE

I.claudius_F2_535_478_1210846_peptide	number	6	962.0757000000001	0	DIVGIDAME

I.claudius_F2_535_478_1210846_peptide	number	7	1290.4896	0	AVRCSAKTGVGIE

I.claudius_F2_535_478_1210846_peptide	number	8	474.5054	0	DVLE

I.claudius_F2_535_478_1210846_peptide	number	9	147.1293	0	E

I.claudius_F2_535_478_1210846_peptide	number	10	937.1341	0	IVAKIPAPE

I.claudius_F2_535_478_1210846_peptide	number	11	6790.756300000001	0	GDPNAPLQALIIDSWFDNYLGVVSLVRIKNGVLRKGDKIKVMSTGQTYNVDRLGIFTPKQE

I.claudius_F2_535_478_1210846_peptide	number	12	676.7132000000001	0	DTTVLE

I.claudius_F2_535_478_1210846_peptide	number	13	307.3235	0	CGE

I.claudius_F2_535_478_1210846_peptide	number	14	3032.3861999999995	0	VGWVVCAIKDILGAPVGDTLTHQHNSATE

I.claudius

In [7]:
l1=[1,2,3,4,5]
for i in l1:
    print(i)

1
2
3
4
5
